>代理地址:183.236.232.160

#### 本次目的是爬取携程旅行的飞机票
###### 分析:
1. 搜索流程的层级关系如下(查询时需要选择):
    单程/往返/多程-->出发地+目的地+出发日期(+返程日期)--->带儿童/婴儿-->直飞/中转/经停-->航空公司-->起抵时间-->机场-->舱位-->机型（大型机/中型机)-->报销凭证(行程单、发票)-->共享航班
2. 数据特征:
   - 出发地
   - 目的地
   - 出发日期
   - 返程日期
   - 起飞时间
   - 抵达时间
   - 单程/往返/多程
   - 直飞/中转/经停
   - 航空公司
   - 机场
   - 舱位
   - 机型
   - 报销凭证
   - 共享航班
   - 出发准点率
   - 到达准点率
   - 优惠（这个比较复杂，有多人优惠、接送优惠、直接减免等等，实在不行就直接以是否存在表示）
   - 退订费用（都是多少元起，所以应该是string类型）
   - 更改费用
   - 转签条件（包含不能转签）
   - 行李额（这个也比较复杂，还需要进一步分析，可以考虑直接存储为string，后期处理）

#### 解析动态请求链接
1. 一个航班的舒适度，获取一个航班的准时率、飞机结构特征、飞机服务（餐食、视频）等等(POST)
> https://flights.ctrip.com/international/search/api/flight/comfort/getFlightComfort?v=0.02213245982064338
2. 一个航班延误信息(GET)
> https://flights.ctrip.com/international/search/api/flight/comfort/getHistoryPunctuality?flightNo=CZ3540&v=0.19936393144728126
3. 目的地目录，对应的区域代码在这里获取(POST)
> https://flights.ctrip.com/international/search/restapi/soa2/15095/json/flightCityPageData?v=0.4043076648877282
4. 城市名称及对应代号、拼音(GET)
> https://flights.ctrip.com/online/api/poi/get?v=0.3694661088668516
5. 航班列表，包含出发地、目的地、wifi、power什么的(POST)
> https://flights.ctrip.com/international/search/api/flight/comfort/batchGetComfortTagList?v=0.26986414538960535
5. 一个航班45天日程，包含出发时间、到达时间（天）、价格、出发城市、到达城市(POST)
> https://flights.ctrip.com/international/search/api/lowprice/calendar/get45DaysCalendarDetailList?v=0.6642750999065998
6. 一次搜索返回的列表，包含所有航班的大致信息，机型、中转、城市等等(POST)
> https://flights.ctrip.com/international/search/api/search/batchSearch?v=0.2018136962837298

In [2]:
import requests

In [3]:
params = {
    "user-agent":"Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/102.0.5005.124 Safari/537.36 Edg/102.0.1245.44"
}

In [9]:
# 获取地方名对应的代号
response = requests.get("https://flights.ctrip.com/online/api/poi/get?v=0.3694661088668516", params=params)

In [18]:
response.json().get("data").get("热门")

[{'display': '北京', 'data': 'Beijing|北京(BJS)|1|BJS'},
 {'display': '上海', 'data': 'Shanghai|上海(SHA)|2|SHA'},
 {'display': '广州', 'data': 'Guangzhou|广州(CAN)|32|CAN'},
 {'display': '深圳', 'data': 'Shenzhen|深圳(SZX)|30|SZX'},
 {'display': '成都', 'data': 'Chengdu|成都(CTU)|28|CTU'},
 {'display': '杭州', 'data': 'Hangzhou|杭州(HGH)|17|HGH'},
 {'display': '武汉', 'data': 'Wuhan|武汉(WUH)|477|WUH'},
 {'display': '西安', 'data': 'Xian|西安(SIA)|10|SIA'},
 {'display': '重庆', 'data': 'Chongqing|重庆(CKG)|4|CKG'},
 {'display': '青岛', 'data': 'Qingdao|青岛(TAO)|7|TAO'},
 {'display': '长沙', 'data': 'Changsha|长沙(CSX)|206|CSX'},
 {'display': '南京', 'data': 'Nanjing|南京(NKG)|12|NKG'},
 {'display': '厦门', 'data': 'Xiamen|厦门(XMN)|25|XMN'},
 {'display': '昆明', 'data': 'Kunming|昆明(KMG)|34|KMG'},
 {'display': '大连', 'data': 'Dalian|大连(DLC)|6|DLC'},
 {'display': '天津', 'data': 'Tianjin|天津(TSN)|3|TSN'},
 {'display': '郑州', 'data': 'Zhengzhou|郑州(CGO)|559|CGO'},
 {'display': '三亚', 'data': 'Sanya|三亚(SYX)|43|SYX'},
 {'display': '济南', 'data': 'Ji

In [1]:
data_json = {
  "flightWayEnum": "OW",
  "arrivalProvinceId": 28,
  "extGlobalSwitches": {
    "useAllRecommendSwitch": True,
    "unfoldPriceListSwitch": True
  },
  "arrivalCountryName": "中国",
  "infantCount": 0,
  "cabin": "Y_S",
  "cabinEnum": "Y_S",
  "departCountryName": "中国",
  "flightSegments": [
    {
      "departureDate": "2022-06-27",
      "arrivalProvinceId": 28,
      "arrivalCountryName": "中国",
      "arrivalCountryCode": "CN",
      "departureCityName": "广州",
      "departureCityCode": "CAN",
      "departureCountryName": "中国",
      "departureCountryCode": "CN",
      "arrivalCityName": "通辽",
      "arrivalCityCode": "TGO",
      "departureCityTimeZone": 480,
      "arrivalCountryId": 1,
      "timeZone": 480,
      "departureCityId": 32,
      "departureCountryId": 1,
      "arrivalCityTimeZone": 480,
      "departureProvinceId": 23,
      "arrivalCityId": 458
    }
  ],
  "childCount": 0,
  "segmentNo": 1,
  "scope": "d",
  "adultCount": 1,
  "extensionAttributes": {
    "LoggingSampling": False,
    "isFlightIntlNewUser": False
  },
  "transactionID": "e98f8f9f65ee43faa2fe1c42633855cb",
  "directFlight": False,
  "departureCityId": 32,
  "isMultiplePassengerType": 0,
  "noRecommend": False,
  "flightWay": "S",
  "arrivalCityId": 458,
  "departProvinceId": 23
}
print(data_json)
# 获取查询结果
response = requests.post("https://flights.ctrip.com/international/search/api/search/batchSearch?v=0.9647383904206186", json=data_json)

response.text

{'flightWayEnum': 'OW', 'arrivalProvinceId': 28, 'extGlobalSwitches': {'useAllRecommendSwitch': True, 'unfoldPriceListSwitch': True}, 'arrivalCountryName': '中国', 'infantCount': 0, 'cabin': 'Y_S', 'cabinEnum': 'Y_S', 'departCountryName': '中国', 'flightSegments': [{'departureDate': '2022-06-27', 'arrivalProvinceId': 28, 'arrivalCountryName': '中国', 'arrivalCountryCode': 'CN', 'departureCityName': '广州', 'departureCityCode': 'CAN', 'departureCountryName': '中国', 'departureCountryCode': 'CN', 'arrivalCityName': '通辽', 'arrivalCityCode': 'TGO', 'departureCityTimeZone': 480, 'arrivalCountryId': 1, 'timeZone': 480, 'departureCityId': 32, 'departureCountryId': 1, 'arrivalCityTimeZone': 480, 'departureProvinceId': 23, 'arrivalCityId': 458}], 'childCount': 0, 'segmentNo': 1, 'scope': 'd', 'adultCount': 1, 'extensionAttributes': {'LoggingSampling': False, 'isFlightIntlNewUser': False}, 'transactionID': 'e98f8f9f65ee43faa2fe1c42633855cb', 'directFlight': False, 'departureCityId': 32, 'isMultiplePasseng

NameError: name 'requests' is not defined

In [28]:
response.json()

{'status': 0,
 'msg': 'success',
 'data': {'context': {'searchId': '',
   'finished': True,
   'flag': 2,
   'showAuthCode': True}}}

In [35]:
'https://flights.ctrip.com/online/list/oneway-can-tgo?depdate=2022-06-27&cabin=y_s_c_f&adult=1&child=0&infant=0'

'https://flights.ctrip.com/online/list/oneway-can-tgo?_=1&depdate=2022-06-27&cabin=Y_S_C_F'

# 成都->温哥华
'https://flights.ctrip.com/international/search/api/search/batchSearch?v=0.713627262411545'
# 成都->首尔
'https://flights.ctrip.com/international/search/api/search/batchSearch?v=0.3155137416049272'
# 成都->广州
'https://flights.ctrip.com/international/search/api/search/batchSearch?v=0.657495352596682'


'https://flights.ctrip.com/international/search/api/search/batchSearch?v=0.657495352596682'

In [47]:
import json

with open("/work/xiecheng/head.json", 'r') as f:
    # json_string = f.read()
    json_dict = json.load(f)
    headers_har = json_dict['headers']
    headers = {}
    for item in headers_har:
        headers[item['name']] = item['value']

    print(headers)


{'Accept': 'application/json', 'Accept-Encoding': 'gzip, deflate, br', 'Accept-Language': 'zh-CN,zh;q=0.9,en;q=0.8,en-GB;q=0.7,en-US;q=0.6', 'Cache-Control': 'no-cache', 'Connection': 'keep-alive', 'Content-Length': '1043', 'Content-Type': 'application/json;charset=UTF-8', 'Cookie': 'MKT_CKID=1655811637254.dubey.k0o6; GUID=09031036218372901773; _RGUID=0ef850db-d62b-429e-bf67-e99e0db385cf; _RDG=2861b8e50e22ee28bb2f1b092914544be8; _RSG=UAqAMlDKux0FNuiDuPwdzB; MKT_Pagesource=PC; _bfaStatusPVSend=1; _gcl_aw=GCL.1655881791.EAIaIQobChMIiP3SqsDA-AIVIcLCBB1CugQjEAAYASAAEgIa4fD_BwE; _gcl_dc=GCL.1655881791.EAIaIQobChMIiP3SqsDA-AIVIcLCBB1CugQjEAAYASAAEgIa4fD_BwE; appFloatCnt=2; nfes_isSupportWebP=1; nfes_isSupportWebP=1; _abtest_userid=b8e50f32-f905-46c4-b565-55659683576f; MKT_CKID_LMT=1655961192005; Union=OUID=index&AllianceID=4897&SID=155952&SourceID=&createtime=1656033778&Expires=1656638578456; MKT_OrderClick=ASID=4897155952&AID=4897&CSID=155952&OUID=index&CT=1656033778458&CURL=https%3A%2F%2Fw

In [78]:
import time



'2022-06-24 13:56:02'

In [85]:
from selenium import webdriver
from selenium.webdriver.common.by import By
import time
from prettytable import PrettyTable


ap_date = ["2022-07-07", "2022-07-10"]
#在此设置出发、到达城市 需要从携程查看相应城市代码
depart_city = "SHA"
arrive_city = "BJS"
#在此设置机票阈值
expect_price = 1000


options = webdriver.ChromeOptions()
# options.add_argument('--headless')
# options.add_argument('--no-sandbox')
# options.add_argument('--disable-gpu')
# options.add_argument('--disable-dev-shm-usage')
browser = webdriver.Chrome("/work/driver/chromedriver", options=options)

js_down = "var q=document.documentElement.scrollTop=10000"
js_top = "var q=document.documentElement.scrollTop=0"
airplane_table = PrettyTable(["航空公司", "出发地", "到达地", "出发时间", "到达时间", "价格"])


for yd_date in ap_date:
    t1 = time.time()
    print(f'[{time.strftime("%Y-%m-%d %H:%M:%S")}]:正在爬取{yd_date}的机票')
    airplane_table.add_row(['----------------', '--------------', yd_date, '-----------', '-----------', '-----------'])

    browser.get(f"https://flights.ctrip.com/online/list/oneway-{depart_city}-{arrive_city}?_=1&depdate={yd_date}")

    browser.execute_script(js_down)  #滚动网页 使得数据加载完毕
    browser.implicitly_wait(5)
    browser.execute_script(js_down)
    browser.implicitly_wait(2)
    browser.execute_script(js_top)
    browser.implicitly_wait(3)
    browser.execute_script(js_down)

    flight_detials = browser.find_elements(By.CLASS_NAME, 'flight-detail')
    flight_prices = browser.find_elements(By.CLASS_NAME, 'flight-operate')
    flight_airlines = browser.find_elements(By.CLASS_NAME, 'flight-airline')

    for i, (flight_detial, flight_price, flight_airline) in enumerate(zip(flight_detials, flight_prices, flight_airlines)):
        flight_detial_text = flight_detial.get_attribute('innerText')
        flight_airline = flight_airline.get_attribute('innerText').split('\n')[0]
        try:  #经停航班会有更多的返回值 不考虑经停航班
            plane_dt, plane_dl, plane_at, plane_al = flight_detial_text.split("\n")
        except:
            continue
        Price = flight_price.get_attribute('innerText').split('\n')[0][1:-1]
        if int(Price) < expect_price:
            airplane_table.add_row([flight_airline, plane_dl, plane_al, plane_dt, plane_at, Price])
    time.sleep(10)
    print(f'[{time.strftime("%Y-%m-%d %H:%M:%S")}]:{yd_date}爬取完成，耗时{time.time() - t1}s')
print(airplane_table)

data_html = airplane_table.get_html_string()
# send_mail(data_html)
browser.close()
# os.system('taskkill /im edgedriver.exe /F')

[2022-06-24 14:13:53]:正在爬取2022-07-07的机票


KeyboardInterrupt: 

In [42]:
import pymysql

db = pymysql.connect(
    host="localhost",
    user="ycj",
    password="000000",
    database="xiecheng",
    charset="utf8"
)


cursor = db.cursor()

In [44]:
data = ["上海航空","FM9107","波音737(中)","1","19:40","22:00","浦东国际机场T1","大兴国际机场","1","424","0","0","0","0","","经济舱"]
sql = "insert into airline_ticket_crawler(airline,al_num,al_type,al_size,departure_time,arrival_time,departure_place,arrival_place,promotion,price,departure_rate,arrival_rate,delay_time,advance_time,devices,cabin) values('{0[0]}','{0[1]}','{0[2]}','{0[3]}','{0[4]}','{0[5]}','{0[6]}','{0[7]}','{0[8]}','{0[9]}','{0[10]}','{0[11]}','{0[12]}','{0[13]}','{0[14]}','{0[15]}')".format(data)
print(sql)
cursor.execute(sql)
db.commit()


insert into airline_ticket_crawler(airline,al_num,al_type,al_size,departure_time,arrival_time,departure_place,arrival_place,promotion,price,departure_rate,arrival_rate,delay_time,advance_time,devices,cabin) values('上海航空','FM9107','波音737(中)','1','19:40','22:00','浦东国际机场T1','大兴国际机场','1','424','0','0','0','0','','经济舱')


In [51]:
import requests

proxy = {
    "https":'https://120.42.46.226:6666',
    "http":'http://120.42.46.226:6666',
}
response = requests.get("http://www.google.com", proxies=proxy)
print(response.text)

<!doctype html><html itemscope="" itemtype="http://schema.org/WebPage" lang="en-PH"><head><meta content="text/html; charset=UTF-8" http-equiv="Content-Type"><meta content="/images/branding/googleg/1x/googleg_standard_color_128dp.png" itemprop="image"><title>Google</title><script nonce="oU7qVmAa2RHrEJ6q65Uzlw">(function(){window.google={kEI:'Fka5YvClJ4OhoAT5-o24Cg',kEXPI:'0,1302536,56873,6059,206,4804,2316,383,246,5,1354,4013,1123753,1197748,653,380089,16115,28684,17572,4859,1361,9291,3029,17579,4020,978,13228,3847,10622,7432,14680,631,5079,1593,1279,2742,149,561,542,840,2197,4100,109,3405,606,2023,1777,520,14670,3227,2845,9,5597,11851,16320,1851,2614,13142,3,576,1014,1,5445,148,11323,991,1661,4,1528,2304,7039,25073,2658,7357,13658,21223,652,5172,2533,4094,4052,3,3541,1,42160,2,16731,11401,11623,5679,1020,2381,2719,18242,2,6,1,7771,4568,6256,23421,830,422,5835,14967,4333,4,6085,1395,445,2,2,1,24626,2006,8155,6582,799,2,2447,593,11638,7341,14455,7,1922,5706,3463,57,553,23,5416,901,547,29

In [98]:
import datetime
ap_date = ["2022-06-28", "2022-07-10"]
start = datetime.datetime.strptime("2022-06-28", "%Y-%m-%d")
end = datetime.datetime.strptime("2022-07-10", "%Y-%m-%d")

(end - start).days

12

以下是成功爬取了batchsearch接口，之前的问题是没有保证v值、header的transactionid以及body（json）当中的transactionid一致

In [14]:
import json

with open("./head.json", "r") as f:
    data = json.load(f)
data

[{'name': ':authority', 'value': 'flights.ctrip.com'},
 {'name': ':method', 'value': 'POST'},
 {'name': ':path',
  'value': '/international/search/api/search/batchSearch?v=0.8974648786273631'},
 {'name': ':scheme', 'value': 'https'},
 {'name': 'accept', 'value': 'application/json'},
 {'name': 'accept-encoding', 'value': 'gzip, deflate, br'},
 {'name': 'accept-language', 'value': 'zh-CN,zh;q=0.9'},
 {'name': 'cache-control', 'value': 'no-cache'},
 {'name': 'content-length', 'value': '1043'},
 {'name': 'content-type', 'value': 'application/json;charset=UTF-8'},
 {'name': 'cookie',
  'value': '_RSG=UBKGEO3yEsAP9xkux4OufA; _RDG=28c2ce45e3fa8428fb3a0480f9e15c7c7e; _RGUID=ad8ef036-0e41-42de-aa78-604ef8bbb259; _bfaStatusPVSend=1; _RF1=114.83.38.117; FlightIntl=Search=[%22CTU|%E6%88%90%E9%83%BD(CTU)|28|CTU|480%22%2C%22CAN|%E5%B9%BF%E5%B7%9E(CAN)|32|CAN|480%22%2C%222022-06-29%22]; GUID=09031160118635094851; _abtest_userid=052b5661-fa9f-43ed-98b5-0fed5ac6058e; _bfi=p1%3D10320673302%26p2%3D103206

In [36]:
header = {}
for i in data:
    header[i['name']] = i['value']

In [37]:
header.pop(':authority')
header.pop(':method')
header.pop(':path')
header.pop(':scheme')
# header.pop('transactionid')
header

{'accept': 'application/json',
 'accept-encoding': 'gzip, deflate, br',
 'accept-language': 'zh-CN,zh;q=0.9',
 'cache-control': 'no-cache',
 'content-length': '1043',
 'content-type': 'application/json;charset=UTF-8',
 'cookie': '_RSG=UBKGEO3yEsAP9xkux4OufA; _RDG=28c2ce45e3fa8428fb3a0480f9e15c7c7e; _RGUID=ad8ef036-0e41-42de-aa78-604ef8bbb259; _bfaStatusPVSend=1; _RF1=114.83.38.117; FlightIntl=Search=[%22CTU|%E6%88%90%E9%83%BD(CTU)|28|CTU|480%22%2C%22CAN|%E5%B9%BF%E5%B7%9E(CAN)|32|CAN|480%22%2C%222022-06-29%22]; GUID=09031160118635094851; _abtest_userid=052b5661-fa9f-43ed-98b5-0fed5ac6058e; _bfi=p1%3D10320673302%26p2%3D10320673302%26v1%3D31%26v2%3D30; _bfaStatus=success; _bfa=1.1656048454332.3xffcg.1.1656385586689.1656390477907.9.32.1; _bfs=1.1; _ubtstatus=%7B%22vid%22%3A%221656048454332.3xffcg%22%2C%22sid%22%3A9%2C%22pvid%22%3A32%2C%22pid%22%3A10320673302%7D',
 'origin': 'https://flights.ctrip.com',
 'referer': 'https://flights.ctrip.com/online/list/oneway-ctu-can?_=1&depdate=2022-06-2

In [47]:
with open("./payload.json", 'r') as f:
    payload = json.load(f)
payload

{'flightWayEnum': 'OW',
 'arrivalProvinceId': 23,
 'extGlobalSwitches': {'useAllRecommendSwitch': True,
  'unfoldPriceListSwitch': True},
 'arrivalCountryName': '中国',
 'infantCount': 0,
 'cabin': 'Y_S_C_F',
 'cabinEnum': 'Y_S_C_F',
 'departCountryName': '中国',
 'flightSegments': [{'departureDate': '2022-06-29',
   'arrivalProvinceId': 23,
   'arrivalCountryName': '中国',
   'arrivalCountryCode': 'CN',
   'departureCityName': '成都',
   'departureCityCode': 'CTU',
   'departureCountryName': '中国',
   'departureCountryCode': 'CN',
   'arrivalCityName': '广州',
   'arrivalCityCode': 'CAN',
   'departureCityTimeZone': 480,
   'arrivalCountryId': 1,
   'timeZone': 480,
   'departureCityId': 28,
   'departureCountryId': 1,
   'arrivalCityTimeZone': 480,
   'departureProvinceId': 22,
   'arrivalCityId': 32}],
 'childCount': 0,
 'segmentNo': 1,
 'scope': 'd',
 'adultCount': 1,
 'extensionAttributes': {'LoggingSampling': False,
  'isFlightIntlNewUser': False},
 'transactionID': '501c2b75b6b144d39def036

In [48]:
response = requests.post("https://flights.ctrip.com/international/search/api/search/batchSearch?v=0.8974648786273631", headers=header, json=payload)

response.json()

{'status': 0,
 'msg': 'success',
 'data': {'context': {'searchId': 'null-0_1', 'finished': True, 'flag': 0},
  'flightItineraryList': [{'itineraryId': 'KY9442_1656471600000',
    'flightSegments': [{'segmentNo': 1,
      'airlineCode': 'KY',
      'airlineName': '昆明航空',
      'crossDays': 0,
      'transferCount': 0,
      'stopCount': 0,
      'duration': 145,
      'leakedVisaTagSwitch': False,
      'flightList': [{'flightNo': 'KY9442',
        'sequenceNo': 1,
        'marketAirlineCode': 'KY',
        'marketAirlineName': '昆明航空',
        'operateAirlineCode': 'ZH',
        'operateAirlineName': '深圳航空',
        'operateFlightNo': 'ZH9442',
        'departureCountryName': '中国',
        'departureProvinceId': 0,
        'departureCityId': 28,
        'departureCityCode': 'CTU',
        'departureCityName': '成都',
        'departureAirportCode': 'TFU',
        'departureAirportName': '成都天府国际机场',
        'departureAirportShortName': '天府',
        'departureTerminal': 'T2',
        'arri

In [52]:
import json

with open("searchlist.json", "r") as f:
    data = json.load(f)
data

{'ResponseStatus': {'Timestamp': '2022-06-28 14:25:00',
  'Ack': 'Success',
  'Errors': [],
  'Build': None,
  'Version': None,
  'Extension': [{'Id': 'CLOGGING_TRACE_ID',
    'Version': None,
    'ContentType': None,
    'Value': '1852099253572939061'},
   {'Id': 'RootMessageId',
    'Version': None,
    'ContentType': None,
    'Value': '100025527-0a70c298-460110-2238183'}]},
 'data': '{"cityMessage":"北京|上海","flightNotes":{"category":1,"noteItemList":[{"content":"{\\"arriveCity\\":\\"SHA\\",\\"departCity\\":\\"BJS\\",\\"departDate\\":\\"2022-06-29\\",\\"lowestPrice\\":606.0,\\"sourceType\\":1,\\"tripType\\":1}","type":1}],"pageType":1},"listCards":[{"airlines":[{"code":"MU","craft":"空客33L(大)","displayName":"东航MU5112","flightAttributes":[],"name":"东方航空","shared":false,"shortName":"东航"}],"arrivalAirportCode":"SHA","arrivalAirportName":"虹桥机场","arrivalName":"虹桥T2","arrivalTime":"15:15","arriveDateTime":"2022-06-29 15:15:00","crossDays":0,"departDateTime":"2022-06-29 13:00:00","departureA

In [102]:
import requests

with open("payload_searchlist.json", "r") as f:
    payload = json.load(f)
payload['head'].pop("extension")
payload['head'].pop("sid")
response = requests.post("https://m.ctrip.com/restapi/soa2/14488/flightList?subEnv=fat128", json=payload)
response.json()

{'ResponseStatus': {'Timestamp': '2022-06-28 15:55:43',
  'Ack': 'Success',
  'Errors': [],
  'Build': None,
  'Version': None,
  'Extension': [{'Id': 'CLOGGING_TRACE_ID',
    'Version': None,
    'ContentType': None,
    'Value': '7783477728534056252'},
   {'Id': 'RootMessageId',
    'Version': None,
    'ContentType': None,
    'Value': '100025527-0a3c7edd-460111-5436620'}]},
 'data': '{"cityMessage":"北京|上海","flightNotes":{"category":1,"noteItemList":[{"content":"{\\"arriveCity\\":\\"SHA\\",\\"departCity\\":\\"BJS\\",\\"departDate\\":\\"2022-06-29\\",\\"lowestPrice\\":615.0,\\"sourceType\\":1,\\"tripType\\":1}","type":1}],"pageType":1},"listCards":[{"airlines":[{"code":"MU","craft":"空客33L(大)","displayName":"东航MU5112","flightAttributes":[],"name":"东方航空","shared":false,"shortName":"东航"}],"arrivalAirportCode":"SHA","arrivalAirportName":"虹桥机场","arrivalName":"虹桥T2","arrivalTime":"15:15","arriveDateTime":"2022-06-29 15:15:00","crossDays":0,"departDateTime":"2022-06-29 13:00:00","departureA

In [79]:
data = response.json()

In [87]:
for k, v in data.items():
    print(f">>>>>>>>{k}:{v}")

>>>>>>>>ResponseStatus:{'Timestamp': '2022-06-28 14:57:19', 'Ack': 'Success', 'Errors': [], 'Build': None, 'Version': None, 'Extension': [{'Id': 'CLOGGING_TRACE_ID', 'Version': None, 'ContentType': None, 'Value': '2765259427055558669'}, {'Id': 'RootMessageId', 'Version': None, 'ContentType': None, 'Value': '100025527-0a70c342-460110-5186654'}]}
>>>>>>>>data:{"cityMessage":"北京|上海","flightNotes":{"category":1,"noteItemList":[{"content":"{\"arriveCity\":\"SHA\",\"departCity\":\"BJS\",\"departDate\":\"2022-06-29\",\"lowestPrice\":615.0,\"sourceType\":1,\"tripType\":1}","type":1}],"pageType":1},"listCards":[{"airlines":[{"code":"MU","craft":"空客33L(大)","displayName":"东航MU5112","flightAttributes":[],"name":"东方航空","shared":false,"shortName":"东航"}],"arrivalAirportCode":"SHA","arrivalAirportName":"虹桥机场","arrivalName":"虹桥T2","arrivalTime":"15:15","arriveDateTime":"2022-06-29 15:15:00","crossDays":0,"departDateTime":"2022-06-29 13:00:00","departureAirportCode":"PEK","departureAirportName":"首都机场","

In [90]:
target = json.loads(data['data'])

In [92]:
for k, v in target.items():
    print(f">>>>>>>>{k}:{v}")

>>>>>>>>cityMessage:北京|上海
>>>>>>>>flightNotes:{'category': 1, 'noteItemList': [{'content': '{"arriveCity":"SHA","departCity":"BJS","departDate":"2022-06-29","lowestPrice":615.0,"sourceType":1,"tripType":1}', 'type': 1}], 'pageType': 1}
>>>>>>>>listCards:[{'airlines': [{'code': 'MU', 'craft': '空客33L(大)', 'displayName': '东航MU5112', 'flightAttributes': [], 'name': '东方航空', 'shared': False, 'shortName': '东航'}], 'arrivalAirportCode': 'SHA', 'arrivalAirportName': '虹桥机场', 'arrivalName': '虹桥T2', 'arrivalTime': '15:15', 'arriveDateTime': '2022-06-29 15:15:00', 'crossDays': 0, 'departDateTime': '2022-06-29 13:00:00', 'departureAirportCode': 'PEK', 'departureAirportName': '首都机场', 'departureName': '首都T2', 'departureTime': '13:00', 'departureWeek': '周三', 'discounts': {'ECONOMY': '经济舱', 'BUSINESS': '公务舱9.9折'}, 'flagTags': [], 'flightTags': {'CRAFT': '大机型', 'MEAT': '有餐食', 'IN_TIME': '准点率97%'}, 'flyMan': 0, 'prices': {'ECONOMY': 1960.0, 'BUSINESS': 7639.0}, 'recommend': False, 'searchKey': 'KLUv/WDpAAU

In [101]:
for k, v in target["listCards"][0].items():
    print(f">>>>>>>>{k}:{v}")

>>>>>>>>airlines:[{'code': 'MU', 'craft': '空客33L(大)', 'displayName': '东航MU5112', 'flightAttributes': [], 'name': '东方航空', 'shared': False, 'shortName': '东航'}]
>>>>>>>>arrivalAirportCode:SHA
>>>>>>>>arrivalAirportName:虹桥机场
>>>>>>>>arrivalName:虹桥T2
>>>>>>>>arrivalTime:15:15
>>>>>>>>arriveDateTime:2022-06-29 15:15:00
>>>>>>>>crossDays:0
>>>>>>>>departDateTime:2022-06-29 13:00:00
>>>>>>>>departureAirportCode:PEK
>>>>>>>>departureAirportName:首都机场
>>>>>>>>departureName:首都T2
>>>>>>>>departureTime:13:00
>>>>>>>>departureWeek:周三
>>>>>>>>discounts:{'ECONOMY': '经济舱', 'BUSINESS': '公务舱9.9折'}
>>>>>>>>flagTags:[]
>>>>>>>>flightTags:{'CRAFT': '大机型', 'MEAT': '有餐食', 'IN_TIME': '准点率97%'}
>>>>>>>>flyMan:0
>>>>>>>>prices:{'ECONOMY': 1960.0, 'BUSINESS': 7639.0}
>>>>>>>>recommend:False
>>>>>>>>searchKey:KLUv/WDpAAUHAAIOLSQwi1YBiJq9dkZpYo0Tm91K4MdsEWgDwl8LTl4H+fyBujAwKBUViKOf7OjnvII4+ukWU3tQPiBHtuEgjlE27oeNV7+DhNxePxiahFeV9SbElgUgAeH65kiUHO09z3Z09UZxsGgYXM+TqYkgjhKe0rFwdYZBwC1FvRN2V19L19LE0ggwRMBCMLbY9Rytu/qAg